## Content
* [1. Loading the Libraries, packages and data, and then cleaning and performing EDA on data](#1)
* [2. Code for the dashboard Interface](#2)
* [3. Code for the underlying functions within the interface](#3)
* [4. Run the dashboard](#4)




<a id='1'></a>
### 1. Loading the Libraries, packages, data, and then cleaning and performing EDA

In [1]:
import plotly.express as px
import panel as pn
pn.extension('plotly')
import locale
locale.setlocale(locale.LC_ALL, 'en_CA.UTF-8')
import warnings
warnings.filterwarnings('ignore')

In [2]:
import plotly.express as px
import hvplot.pandas
import matplotlib.pyplot as plt
from panel.interact import interact
from panel import widgets
import numpy as np
import pandas as pd
import datetime as dt
from IPython.display import display
import pandas_datareader as pdr
import time
from scipy.optimize import minimize
import plotly.graph_objects as go


Bad key "text.kerning_factor" on line 4 in
C:\Users\Mohammed\anaconda3\envs\pyvizenv\lib\site-packages\matplotlib\mpl-data\stylelib\_classic_test_patch.mplstyle.
You probably need to get an updated matplotlibrc file from
http://github.com/matplotlib/matplotlib/blob/master/matplotlibrc.template
or from the matplotlib source distribution


In [3]:
tickers = ['QQQ','VOO','VTI','GDX','IWM','BND','XLE','IVV','AGG','VTV','TLT','IBB','GLD','SPY','VGK','VWO','IJH','QID','SHY','SQQQ','VEA','EFA','IWF','IJR']

In [4]:
start_date = (dt.date.today() - dt.timedelta(10*365)).isoformat()
end_date = dt.date.today().isoformat()
close_prices_rawdata = pd.DataFrame(columns=tickers)
for ticker in tickers:
    close_prices_rawdata[ticker] = pdr.DataReader(ticker,'yahoo',start_date,end_date)['Adj Close']

In [5]:
close_prices_rawdata.isnull().sum() / close_prices_rawdata.shape[0] * 100

QQQ     0.0
VOO     0.0
VTI     0.0
GDX     0.0
IWM     0.0
BND     0.0
XLE     0.0
IVV     0.0
AGG     0.0
VTV     0.0
TLT     0.0
IBB     0.0
GLD     0.0
SPY     0.0
VGK     0.0
VWO     0.0
IJH     0.0
QID     0.0
SHY     0.0
SQQQ    0.0
VEA     0.0
EFA     0.0
IWF     0.0
IJR     0.0
dtype: float64

In [6]:
close_prices_rawdata.fillna(method='bfill',inplace=True)

In [7]:
close_prices_rawdata.describe()

QQQ          VOO          VTI          GDX          IWM  \
count  2516.000000  2516.000000  2516.000000  2516.000000  2516.000000   
mean    122.261163   184.221721   103.247316    29.102597   114.493527   
std      61.959764    63.812486    35.233742    12.035042    32.040697   
min      45.385269    83.746513    46.678661    12.119957    53.310043   
25%      69.255756   131.179874    74.041080    21.142088    90.330502   
50%     104.685379   172.276703    97.239845    23.876971   110.658054   
75%     164.960266   237.147175   132.958839    36.750618   144.502975   
max     319.029999   350.420013   199.250000    62.370876   208.169998   

               BND          XLE          IVV          AGG          VTV  ...  \
count  2516.000000  2516.000000  2516.000000  2516.000000  2516.000000  ...   
mean     72.301855    55.824120   201.418823    97.317419    75.673719  ...   
std       6.532035     9.162663    69.595182     8.779148    22.727966  ...   
min      60.121243    22.482656    91.733398    80.481247    35.731281  ...   
25%      67.485228    52.393909   143.411415    90.830072    57.084381  ...   
50%      71.419220    56.242691   189.118111    96.504673    72.859356  ...   
75%      74.697157    61.409876   259.023804   100.662336    97.357964  ...   
max      88.582695    78.235291   382.640015   118.700294   122.160004  ...   

               VGK          VWO          IJH          QID          SHY  \
count  2516.000000  2516.000000  2516.000000  2516.000000  2516.000000   
mean     44.453436    35.955208   139.363325   218.076212    80.033747   
std       7.204841     4.471860    40.093541   236.157803     2.452745   
min      27.771158    25.015079    64.635521     6.830000    76.601471   
25%      39.335575    32.871521   106.890120    41.589867    78.291100   
50%      44.646891    35.421139   136.831909   121.655212    79.499569   
75%      50.485944    38.929871   177.831207   332.357468    80.150513   
max      62.779999    52.459999   241.259995   957.534363    86.396912   

               SQQQ          VEA          EFA          IWF          IJR  
count   2516.000000  2516.000000  2516.000000  2516.000000  2516.000000  
mean    5950.156181    33.716901    53.744307   105.970012    55.807530  
std     9202.202333     5.624079     8.415274    45.334407    17.153863  
min       14.340000    21.725838    35.177601    45.244984    24.440947  
25%      287.594757    29.631617    47.705679    68.752920    42.685280  
50%     1551.237793    33.446848    53.755062    94.422134    53.655691  
75%     7659.380737    38.672315    61.077036   138.183521    72.006981  
max    41304.878906    49.139999    75.730003   244.190002    98.529999  

[8 rows x 24 columns]

In [8]:
close_prices_rawdata.info()

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 2516 entries, 2011-01-11 to 2021-01-08
Data columns (total 24 columns):
QQQ     2516 non-null float64
VOO     2516 non-null float64
VTI     2516 non-null float64
GDX     2516 non-null float64
IWM     2516 non-null float64
BND     2516 non-null float64
XLE     2516 non-null float64
IVV     2516 non-null float64
AGG     2516 non-null float64
VTV     2516 non-null float64
TLT     2516 non-null float64
IBB     2516 non-null float64
GLD     2516 non-null float64
SPY     2516 non-null float64
VGK     2516 non-null float64
VWO     2516 non-null float64
IJH     2516 non-null float64
QID     2516 non-null float64
SHY     2516 non-null float64
SQQQ    2516 non-null float64
VEA     2516 non-null float64
EFA     2516 non-null float64
IWF     2516 non-null float64
IJR     2516 non-null float64
dtypes: float64(24)
memory usage: 491.4 KB


In [9]:
# Initial Weights
num_assets = len(tickers)
init_weights = num_assets * [1 / num_assets]

returns = close_prices_rawdata.pct_change().dropna()
log_returns = np.log(close_prices_rawdata/close_prices_rawdata.shift(1)).dropna()

bounds = tuple((0,1) for i in range(len(close_prices_rawdata.columns)))
init_weights = [1/(len(close_prices_rawdata.columns))] * (len(close_prices_rawdata.columns))

split_row = int(close_prices_rawdata.shape[0] * 0.8)
test_data = close_prices_rawdata.iloc[split_row:]

close_prices_rawdata = close_prices_rawdata.iloc[0:split_row]

# Calculate estimated return for each stock
individual_returns = returns.mean() * 252
#display(individual_returns)
# Estimate individual stock risks for comparison
individual_risks = np.std(returns) * np.sqrt(252)
#display(individual_risks)
individual_analysis = pd.concat([individual_returns,individual_risks],axis=1)
individual_analysis.columns = ['Returns','Risks']
individual_analysis['Sharpe_Ratios'] = individual_analysis.Returns / individual_analysis.Risks

sorted_securities = individual_analysis.sort_values(by='Returns', ascending = False)

mkt = pdr.DataReader('^GSPC','yahoo',start_date,end_date)['Adj Close']
mkt_data = mkt.iloc[split_row:]
mkt_returns = mkt_data.fillna(method='bfill').pct_change().dropna()

allo_dict = {
    "Very Aggressive": {"Stocks" : "90%", "Bonds" : "10%", "Cash": "0%"},
    "Aggressive": {"Stocks" : "70%", "Bonds" : "25%", "Cash": "5%"},
    "Moderate & Balanced": {"Stocks" : "50%", "Bonds" : "40%", "Cash": "10%"},
    "Conservative": {"Stocks" : "35%", "Bonds" : "50%", "Cash": "15%"},
    "Very Conservative": {"Stocks" : "20%", "Bonds" : "60%", "Cash": "20%"}
}


In [10]:
def get_portfolio_type(total):
    if  total >= 26: return "Very Aggressive"
    elif  26 > total >= 21: return "Aggressive"
    elif  21 > total >= 15: return "Moderate & Balanced"
    elif  15 > total >= 8: return "Conservative"
    elif  8 > total: return "Very Conservative"

In [11]:
def check_sum(weights):
    weights = np.array(weights)
    #return 0 if sum of the weights is 1
    return np.sum(weights)-1

In [12]:
def minimize_volatility(weights):
    weights = np.array(weights)
    return np.sqrt(np.dot(weights.T, np.dot(log_returns.cov()*252, weights)))
    # return np.sqrt(np.dot(weights, np.dot(returns.cov(), weights)) * 252)

In [13]:
def calculate_return(weights):
    weights = np.array(weights)
    return np.sum(log_returns.mean() * weights) * 252
    # return np.dot(returns.mean(), weights) * 252
    # return np.sum(returns.mean() * weights) * 252

In [14]:
def calculate_sharpe(weights):
    weights = np.array(weights)
    return calculate_return(weights) / calculate_std_dev(weights)

In [15]:
def negative_sharpe(weights):
    weights = np.array(weights)
    return calculate_sharpe(weights) * -1
    #return -calculate_sharpe(w)

In [16]:
def maximize_return(weights):
    weights = np.array(weights)
    return calculate_return(weights) * -1
    # return np.dot(returns.mean(), weights) * 252
    # return np.sum(returns.mean() * weights) * 252

In [17]:
def calculate_std_dev(weights):
    weights = np.array(weights)
    return np.sqrt(np.dot(weights.T, np.dot(returns.cov(), weights)) * 252)

In [18]:
def negative_return(w):
    return -calculate_return(w)

In [19]:
def print_weights(weights):
    w = [round(i*100,2)for i in weights]
    w = pd.DataFrame(w, columns = ['Weight (%)'], index = returns.columns)
    #print("\n",w[w['Weight (%)']>0])
    new_w = w[w['Weight (%)']>0]
    return new_w

In [20]:
# Get minimum and maximum risk possible given the asset universe
cons_min_risk = {'type':'eq','fun': check_sum}
min_risk = round(minimize(fun=minimize_volatility, x0=init_weights, bounds=bounds,constraints=cons_min_risk)['fun'],3)
max_risk = round(individual_risks.max(),3)
all_risks = np.linspace(min_risk,max_risk).round(3)

start = time.time()

max_returns = []
weights_min_vol_max_ret = []
for each_risk_num in all_risks: 
    cons_returns = ({'type':'eq', 'fun': lambda w: w.sum() - 1},
                    {'type':'eq', 'fun': lambda w: minimize_volatility(w) - each_risk_num})   
    ret_given_risk_results = minimize(maximize_return, x0=init_weights, bounds = bounds, constraints = cons_returns)
    max_returns.append(calculate_return(ret_given_risk_results['x']))
    weights_min_vol_max_ret.append(ret_given_risk_results['x'])
    
max_return_volatility = minimize_volatility(weights_min_vol_max_ret[np.argmax(max_returns)])
frontier_return = np.linspace(0,max_return_volatility,100)

frontier_volatility = []
weights_array = []
returns_array = []

for possible_return in frontier_return:
    cons_risk = ({'type':'eq', 'fun':check_sum},
                 {'type':'eq', 'fun': lambda w: calculate_return(w) - possible_return})
    
    results = minimize(minimize_volatility,init_weights,method='SLSQP', bounds=bounds, constraints=cons_risk)
    frontier_volatility.append(results['fun'])
    weights_array.append(results['x'])
    returns_array.append(calculate_return(results['x']))

ef_df = pd.DataFrame({'Returns':returns_array, 'Volatility':frontier_volatility})
ef_df['Sharpe'] = ef_df['Returns'] /  ef_df['Volatility']
ef_df_pos_sharpe = ef_df[ef_df['Sharpe']>= 1]
opt_sharpe = ef_df_pos_sharpe[ef_df_pos_sharpe.Sharpe == ef_df_pos_sharpe.Sharpe.max()]

print('Elapsed Time: %.2f seconds' % (time.time() - start))

Elapsed Time: 736.34 seconds


In [21]:
# Set constrains and initial guess for optimal Sharpe
cons_opt_sharpe = {'type': 'eq', 'fun': lambda w: w.sum() - 1}

opt_results = minimize(negative_sharpe, x0=init_weights, bounds = bounds, constraints=cons_opt_sharpe)
opt_w = opt_results['x']

print("Computational Optimized weights:")
print_weights(opt_w)
print("\n")
print("Indicators of Optimal Portfolio:")
print("Return {:.3f}, Volatility {:.3f}, Sharpe {:.3f}".format(calculate_return(opt_w), calculate_std_dev(opt_w),calculate_sharpe(opt_w)))

Computational Optimized weights:


Indicators of Optimal Portfolio:
Return 0.019, Volatility 0.010, Sharpe 1.866


In [22]:
# Set constrains and initial guess for minimum variance
cons_opt_var = {'type':'eq','fun': lambda w: np.sum(w) - 1}
opt_var_results = minimize(fun=calculate_std_dev,bounds=bounds,x0=init_weights,constraints=cons_opt_var)
opt_var_w = opt_var_results['x']
print("Computational Optimized weights:")
print_weights(opt_var_w)
print("\n")
print("Indicators of Minimum Variance Portfolio:")
print("Return {:.3f}, Volatility {:.3f}, Sharpe {:.3f}".format(calculate_return(opt_var_w), calculate_std_dev(opt_var_w),calculate_sharpe(opt_var_w)))

Computational Optimized weights:


Indicators of Minimum Variance Portfolio:
Return -0.027, Volatility 0.005, Sharpe -5.874


In [23]:
start = time.time()

#calculate mean daily return and covariance of daily returns
mean_daily_returns = returns.mean()
# cov_matrix = returns.cov() * 252
cov_matrix = returns.cov()

#set number of runs of random portfolio weights
num_portfolios = num_assets * 2000

#set up array to hold results
results = np.zeros((num_portfolios,3+num_assets))
portfolio_returns_records = [] # Define an empty array for portfolio returns
portfolio_volatility_records = [] # Define an empty array for portfolio volatility
portfolio_weights_records = [] # Define an empty array for asset weights
portfolio_sharpe_ratio_records = []# Define an empty list for sharpe ratios

for i in range(num_portfolios):
    #select random weights for portfolio holdings
    # weights = np.random.dirichlet(np.ones(num_assets),size=1)
    mc_weights = np.array(np.random.random(num_assets))
    #rebalance weights to sum to 1
    mc_weights /= np.sum(mc_weights)
    
    #calculate portfolio return and volatility
    portfolio_return = np.sum(mean_daily_returns * mc_weights) * 252
    #port_ret = np.sum(log_ret.mean() * wts)
    #port_ret = (port_ret + 1) ** 252 - 1
    portfolio_std_dev = np.sqrt(np.dot(np.transpose(mc_weights),np.dot(cov_matrix, mc_weights))) * np.sqrt(252)
    
    #store results in results array
    results[i,0] = portfolio_return
    results[i,1] = portfolio_std_dev
    #store Sharpe Ratio (return / volatility) - risk free rate element excluded for simplicity
    results[i,2] = results[i,0] / results[i,1]
    #iterate through the weight vector and add data to results array
    for j in range(len(mc_weights)):
        results[i,j+3] = mc_weights[j]
    portfolio_returns_records.append(portfolio_return)
    portfolio_volatility_records.append(portfolio_std_dev)
    portfolio_weights_records.append(mc_weights)
    portfolio_sharpe_ratio_records.append(results[i,2])

#convert results array to Pandas DataFrame
portfolio_returns_records = np.array(portfolio_returns_records) 
portfolio_volatility_records = np.array(portfolio_volatility_records)
portfolio_weights_records = np.array(portfolio_weights_records)
portfolio_sharpe_ratio_records = np.array(portfolio_sharpe_ratio_records)
stocks_weights = [f'{stock} weight' for stock in returns.columns.tolist()]
# for counter, symbol in enumerate(closes.columns.tolist()):
#     [symbol+' weight'] = [w[counter] for w in p_weights]
column_order = ['Returns', 'Volatility', 'Sharpe_Ratios'] + [stock+' Weight' for stock in tickers]    
results_frame = pd.DataFrame(results,columns=column_order)

plot_boundary = results_frame.Volatility.max()
sct_data = results_frame[results_frame.Volatility <= plot_boundary]
ef_data = ef_df[ef_df.Volatility <= plot_boundary]
min_var_df = pd.DataFrame({'Volatility':[calculate_std_dev(opt_var_w)],'Returns':[calculate_return(opt_var_w)]})

sct_plot = sct_data.hvplot.scatter(x="Volatility",y="Returns",title="Effecient Frontier",c="Sharpe_Ratios",cmap='RdYlBu')
ef_plot = ef_data.hvplot(x="Volatility",y="Returns", line_width=3, line_dash='dashed')
opt_shp_plot = opt_sharpe.hvplot.scatter(x="Volatility",y="Returns",label='Optimal Sharpe',s=100,color='green')
min_var_plot = min_var_df.hvplot.scatter(x="Volatility",y="Returns",label='Minimum Variance',s=100, color='yellow')

print('Elapsed Time: %.2f seconds' % (time.time() - start))


Elapsed Time: 18.51 seconds


In [24]:
def get_goal_plot(goal_risk):
    
    goal_risk = round(float(goal_risk),3)
    goal_cons = ({'type':'eq', 'fun': lambda w: w.sum() - 1},
                 {'type':'eq', 'fun': lambda w: calculate_std_dev(w) - goal_risk})
    opt_goal = minimize(negative_return, x0=init_weights, bounds = bounds, constraints=goal_cons)
    opt_goal_weights = opt_goal['x']
    goal_df = pd.DataFrame({'Risk': [calculate_std_dev(opt_goal_weights)],'Return': [calculate_return(opt_goal_weights)]})
    goal_plot = goal_df.hvplot.scatter(x="Risk",y="Return",label='Goal Portfolio',s=100,color='red')
    all_plot = (sct_plot * ef_plot * goal_plot * min_var_plot * opt_shp_plot).opts(legend_position='top_left')
    return all_plot

In [25]:
def get_goal_allo(goal_risk):
    goal_risk = round(float(goal_risk),3)
    goal_cons = ({'type':'eq', 'fun': lambda w: w.sum() - 1},
                 {'type':'eq', 'fun': lambda w: calculate_std_dev(w) - goal_risk})
    opt_goal = minimize(negative_return, x0=init_weights, bounds = bounds, constraints=goal_cons)
    opt_goal_weights = opt_goal['x']
    #print("Computational Optimized weights for our risk goal:")
    goal_allo = print_weights(opt_goal_weights)
    #print("\n")
    #print("Indicators of Optimal Portfolio given our risk goal:")
    #print("Return {:.3f}, Volatility {:.3f}, Sharpe {:.3f}".format(calculate_return(opt_goal_weights), calculate_std_dev(opt_goal_weights),calculate_sharpe(opt_goal_weights)))
    return goal_allo    

In [26]:
def get_backtest_plot(goal_risk):
    
    goal_risk = round(float(goal_risk),3)
    goal_cons = ({'type':'eq', 'fun': lambda w: w.sum() - 1},
                 {'type':'eq', 'fun': lambda w: calculate_std_dev(w) - goal_risk})
    opt_goal = minimize(negative_return, x0=init_weights, bounds = bounds, constraints=goal_cons)
    opt_goal_weights = opt_goal['x']
        
    mkt_cum_rets = (1 + mkt_returns).cumprod()
    goal_portfolio_returns = test_data.pct_change().dropna().dot(opt_goal_weights)
    cummulative_returns = (1 + goal_portfolio_returns).cumprod()
    
    plt1 = (cummulative_returns*100000).hvplot(c='darkorange', line_width=3,label='Portfolio') 
    plt2 = (mkt_cum_rets*100000).hvplot(c='red', line_width=3,label='Market')
    combplt = (plt1 * plt2).opts(legend_position='top_left',title = 'Backtesting Portfolio value of $100k investment',yformatter='%.00f')
    
    return combplt



#     fig2 = go.Figure()
#     fig2.add_trace(
#         go.Scatter(x=((cummulative_returns*100000).index), y=(cummulative_returns*100000),name='Portfolio',line_width=3)
#     )
#     fig2.add_trace(
#         go.Scatter(x=((mkt_cum_rets*100000).index), y=(mkt_cum_rets*100000),name='Market',line_width=3)
#     )
#     fig2.update_layout(
#         title = "Backtesting Portfolio value of $100k investment",
#         xaxis_title = 'Date',
#         yaxis_title = 'Cummulative Returns'
#     )
    
#    return fig2

<a id='2'></a>
## 2. Code for the dashboard Interface

In [27]:
rsp_ques_row = pn.Row(  pn.pane.Pane("Option 1: Take out money immediately",sizing_mode='scale_width',), 
                        pn.pane.Pane("Option 2: Move money to other investments",sizing_mode='scale_width'),
                        pn.pane.Pane("Option 3: Concerned but wait a  bit more to see if things improved",sizing_mode='scale_width'),
                        pn.pane.Pane("Option 4: Expected Risk and market downturn, leave money in place and expect things to improve",sizing_mode='scale_width'),
                        pn.pane.Pane("Option 5: Can tolerate higher degrees of fluctuation in the value, to invest more expecting future growth",sizing_mode='scale_width'),
                        width=1000,) 
age_ques_row = pn.Row(  pn.pane.Pane("Option 1: Above 60 years",sizing_mode='scale_width'), 
                        pn.pane.Pane("Option 2: Between 50 and 60 years",sizing_mode='scale_width'),
                        pn.pane.Pane("Option 3: Between 40 and 50 years",sizing_mode='scale_width'),
                        pn.pane.Pane("Option 4: Between 30 and 40 years",sizing_mode='scale_width'),
                        pn.pane.Pane("Option 5: Between 20 and 30 years",sizing_mode='scale_width'),
                        width=1000)  
hzn_ques_row = pn.Row(  pn.pane.Pane("Option 1: <= 1 year",sizing_mode='scale_width'), 
                        pn.pane.Pane("Option 2: > 1 year and <= 3 years",sizing_mode='scale_width'),
                        pn.pane.Pane("Option 3: > 3 years and <= 5 years",sizing_mode='scale_width'),
                        pn.pane.Pane("Option 4: > 5 years and <= 7 years",sizing_mode='scale_width'),
                        pn.pane.Pane("Option 5: > 7 years",sizing_mode='scale_width'),
                        width=1000)  
gol_ques_row = pn.Row(  pn.pane.Pane("Option 1: Minimize Risk, preservation of capital even if not meeting inflation",sizing_mode='scale_width'), 
                        pn.pane.Pane("Option 2: Modest appreciation with atleast meeting inflation",sizing_mode='scale_width'),
                        pn.pane.Pane("Option 3: Periodic Income",sizing_mode='scale_width'),
                        pn.pane.Pane("Option 4: Some Growth + Periodic Income",sizing_mode='scale_width'),
                        pn.pane.Pane("Option 5: High Returns and Investment Growth",sizing_mode='scale_width'),
                        width=1000)
knw_ques_row = pn.Row(  pn.pane.Pane("Option 1: First time investor. No familiarity or interest",sizing_mode='scale_width'), 
                        pn.pane.Pane("Option 2: Little familiarity",sizing_mode='scale_width'),
                        pn.pane.Pane("Option 3: Understand the importance of diversification",sizing_mode='scale_width'),
                        pn.pane.Pane("Option 4: Understand market fluctuation, different market sectors and growth characteristics requirements",sizing_mode='scale_width'),
                        pn.pane.Pane("Option 5: Experienced with all investment classes",sizing_mode='scale_width'),
                        width=1000)                      
ret_ques_row = pn.Row(  pn.pane.Pane("Option 1: Inflation + <=1%",sizing_mode='scale_width'), 
                        pn.pane.Pane("Option 2: Inflation + >1% & <=3%",sizing_mode='scale_width'),
                        pn.pane.Pane("Option 3: Inflation + >3% & <=6%",sizing_mode='scale_width'),
                        pn.pane.Pane("Option 4: Inflation + >6% & <=9%",sizing_mode='scale_width'),
                        pn.pane.Pane("Option 5: Inflation + >9%",sizing_mode='scale_width'),
                        width=1000)  

age_radio = pn.widgets.RadioButtonGroup(options=['Option 1','Option 2','Option 3','Option 4','Option 5'],width=1000,button_type='primary')
hzn_radio = pn.widgets.RadioButtonGroup(options=['Option 1','Option 2','Option 3','Option 4','Option 5'],width=1000,button_type='primary')
gol_radio = pn.widgets.RadioButtonGroup(options=['Option 1','Option 2','Option 3','Option 4','Option 5'],width=1000,button_type='primary')
rsp_radio = pn.widgets.RadioButtonGroup(options=['Option 1','Option 2','Option 3','Option 4','Option 5'],width=1000,button_type='primary')
ret_radio = pn.widgets.RadioButtonGroup(options=['Option 1','Option 2','Option 3','Option 4','Option 5'],width=1000,button_type='primary')
knw_radio = pn.widgets.RadioButtonGroup(options=['Option 1','Option 2','Option 3','Option 4','Option 5'],width=1000,button_type='primary')

age_col = pn.Column('Choose your Age bracket:',age_ques_row,age_radio,pn.panel('<hr></hr>',sizing_mode='stretch_width'))
hzn_col = pn.Column('What is your Investment Horizon:',hzn_ques_row,hzn_radio,pn.panel('<hr></hr>',sizing_mode='stretch_width'))
gol_col = pn.Column('What is your Investment Goal:',gol_ques_row,gol_radio,pn.panel('<hr></hr>',sizing_mode='stretch_width'))
rsp_col = pn.Column('In case of 20% decline in your portfolio value, you would:',rsp_ques_row,rsp_radio,pn.panel('<hr></hr>',sizing_mode='stretch_width'))
ret_col = pn.Column('What is your expected return on your investment:',ret_ques_row,ret_radio,pn.panel('<hr></hr>',sizing_mode='stretch_width'))
knw_col = pn.Column('How familiar are you with investing in Financial markets:',knw_ques_row,knw_radio,pn.panel('<hr></hr>',sizing_mode='stretch_width'))

get_risk_btn = pn.widgets.Button(name='Get_Risk_Score',button_type='primary')

step1_layout = pn.Column(age_col,hzn_col,gol_col,rsp_col,ret_col,knw_col,get_risk_btn)

In [28]:
risk_txtbox = pn.widgets.TextInput(name='Risk_Score', value='',width=300)
risk_slider = pn.widgets.FloatSlider(name='Risk_Slider',start = min_risk, end = max_risk,width=300)
refresh_btn = pn.widgets.Button(name='🔄',width=20)
row1 = pn.Row(risk_slider,risk_txtbox,refresh_btn)
row2 = pn.Row(get_goal_allo(risk_slider.value),get_goal_plot(risk_slider.value))
row3 = pn.Row(get_backtest_plot(risk_slider.value))
step2_layout = pn.Column(row1,row2,row3)

In [29]:
def click_event(event):
    total = int(age_radio.value[-1]) + int(knw_radio.value[-1]) + int(gol_radio.value[-1]) + int(rsp_radio.value[-1]) + int(ret_radio.value[-1]) + int(hzn_radio.value[-1])
    risk_score_quantile = round(total / 30,3)
    
    risk = np.percentile(ef_df_pos_sharpe.Volatility,q=(risk_score_quantile*100))
    risk_slider.value = risk.round(3)
    risk_txtbox.value = str(risk.round(3))
    dashboard[1][1][1][0] = get_goal_allo(risk_slider.value)
    dashboard[1][1][1][1] = get_goal_plot(risk_slider.value)
    dashboard[1][1][2][0] = get_backtest_plot(risk_slider.value)



In [30]:
#@pn.depends(risk_slider.param.direction)
def update_dashboard(event):
    
    risk_txtbox.value = str(risk_slider.value)
    dashboard[1][1][1][0] = get_goal_allo(risk_slider.value)
    dashboard[1][1][1][1] = get_goal_plot(risk_slider.value)
    dashboard[1][1][2][0] = get_backtest_plot(risk_slider.value)


<a id='3'></a>
## 3. Code for the underlying functions within the interface

The steps performed are as follows: 

1) Calculating the risk score, based on client answers

2) Using markovitz mean variance analysis to recommend optimal portfolio for client given the risk score

3) Producing charts for the effecient frontier and portfolio backtesting performance

#### Click the url produced by this code to see the dashboard

In [31]:
#pn.state.add_periodic_callback(update_dashboard,period=1000)
get_risk_btn.on_click(click_event)

In [32]:
refresh_btn.on_click(update_dashboard)

<a id='4'></a>
## 4. Code for the dashboard Interface

In [33]:
# Create a Title for the Dashboard
dashboard_title = '## Robo Advisor Dashboard'
tabs = pn.Tabs(('Step 1- Enter Investor Characteristics',step1_layout),('Step 2- Portfolio Recommendation',step2_layout))
dashboard = pn.Column(dashboard_title,tabs)
dashboard

Column
    [0] Markdown(str)
    [1] Tabs
        [0] Column
            [0] Column
                [0] Markdown(str)
                [1] Row(width=1000)
                    [0] Markdown(str, sizing_mode='scale_width')
                    [1] Markdown(str, sizing_mode='scale_width')
                    [2] Markdown(str, sizing_mode='scale_width')
                    [3] Markdown(str, sizing_mode='scale_width')
                    [4] Markdown(str, sizing_mode='scale_width')
                [2] RadioButtonGroup(button_type='primary', options=['Option 1', 'Option 2', ...], value='Option 1', width=1000)
                [3] Markdown(str, sizing_mode='stretch_width')
            [1] Column
                [0] Markdown(str)
                [1] Row(width=1000)
                    [0] Markdown(str, sizing_mode='scale_width')
                    [1] Markdown(str, sizing_mode='scale_width')
                    [2] Markdown(str, sizing_mode='scale_width')
                    [3] Markdown(str, sizing_mode='scale_width')
                    [4] Markdown(str, sizing_mode='scale_width')
                [2] RadioButtonGroup(button_type='primary', options=['Option 1', 'Option 2', ...], value='Option 1', width=1000)
                [3] Markdown(str, sizing_mode='stretch_width')
            [2] Column
                [0] Markdown(str)
                [1] Row(width=1000)
                    [0] Markdown(str, sizing_mode='scale_width')
                    [1] Markdown(str, sizing_mode='scale_width')
                    [2] Markdown(str, sizing_mode='scale_width')
                    [3] Markdown(str, sizing_mode='scale_width')
                    [4] Markdown(str, sizing_mode='scale_width')
                [2] RadioButtonGroup(button_type='primary', options=['Option 1', 'Option 2', ...], value='Option 1', width=1000)
                [3] Markdown(str, sizing_mode='stretch_width')
            [3] Column
                [0] Markdown(str)
                [1] Row(width=1000)
                    [0] Markdown(str, sizing_mode='scale_width')
                    [1] Markdown(str, sizing_mode='scale_width')
                    [2] Markdown(str, sizing_mode='scale_width')
                    [3] Markdown(str, sizing_mode='scale_width')
                    [4] Markdown(str, sizing_mode='scale_width')
                [2] RadioButtonGroup(button_type='primary', options=['Option 1', 'Option 2', ...], value='Option 1', width=1000)
                [3] Markdown(str, sizing_mode='stretch_width')
            [4] Column
                [0] Markdown(str)
                [1] Row(width=1000)
                    [0] Markdown(str, sizing_mode='scale_width')
                    [1] Markdown(str, sizing_mode='scale_width')
                    [2] Markdown(str, sizing_mode='scale_width')
                    [3] Markdown(str, sizing_mode='scale_width')
                    [4] Markdown(str, sizing_mode='scale_width')
                [2] RadioButtonGroup(button_type='primary', options=['Option 1', 'Option 2', ...], value='Option 1', width=1000)
                [3] Markdown(str, sizing_mode='stretch_width')
            [5] Column
                [0] Markdown(str)
                [1] Row(width=1000)
                    [0] Markdown(str, sizing_mode='scale_width')
                    [1] Markdown(str, sizing_mode='scale_width')
                    [2] Markdown(str, sizing_mode='scale_width')
                    [3] Markdown(str, sizing_mode='scale_width')
                    [4] Markdown(str, sizing_mode='scale_width')
                [2] RadioButtonGroup(button_type='primary', options=['Option 1', 'Option 2', ...], value='Option 1', width=1000)
                [3] Markdown(str, sizing_mode='stretch_width')
            [6] Button(button_type='primary', name='Get_Risk_Score')
        [1] Column
            [0] Row
                [0] FloatSlider(end=0.584, name='Risk_Slider', start=0.006, value=0.006, value_throttled=0.006, width=300)
                [1] TextInput(name='Risk_Score',